
$a_h(u_h, v_h) + b_h(v_h, p_h)-b_h(u_h, q_h)+ s_h(p_h, q_h)=\int_\Omega f\cdot v_h\,\forall v_h \in U_h, \forall q_h \in P_h,$

where the discrete bilinear form $a_h$ is defined by $a_h=\sum\limits_{i=1}^d a^{sip}_h (v_{h,i}, w_{h,i})$ with \begin{align*}
a^{sip}_h (v_{h,i}, w_{h,i})& =\int_\Omega\nabla_h v_{h,i}\cdot\nabla_h w_{h,i} + \sum\limits_{F\in\mathcal{F}_h}\frac{\eta}{h_F}[[v_{h,i}]][[w_{h,i}]]\\
&\quad-\sum\limits_{F\in\mathcal{F_h}}\int_F (\{\{\nabla_hv_{h,i}\}\}\cdot n_F[[w_{h,i}]] + [[v_{h,i}]]\{\{\nabla_hw_{h,i}\}\}\cdot n_F),
\end{align*} the discrete bilinear form $b_h$ by 
$$b_h(v_h,q_h) = -\int_\Omega q_h\nabla_h\cdot v_h + \sum\limits_{F\in F_h}\int_F[[v_h]]\cdot n_F\{\{q_h\}\},$$ and where
$s_h(q_h, r_h):=\sum\limits_{F\in \mathcal{F}^i_h}h_F\int_F[[q_h]][[r_h]].$


In [18]:
import netgen.gui
from netgen.geom2d import unit_square
from ngsolve import *
import numpy as np


mesh = Mesh(unit_square.GenerateMesh(maxh=0.2))
Draw(mesh)
mesh.nv, mesh.ne   # number of vertices & elements

V = VectorL2(mesh,order=2, dirichlet ='left|right|top|bottom',dgjumps=True)
Q = L2(mesh,order=1)
X = FESpace([V,Q],dgjumps=True)
gfu = GridFunction(X)
(u,p), (v,q) = X.TnT()

n = specialcf.normal(mesh.dim)
h = specialcf.mesh_size        
# Penalty parameter
eta=1
#gradient u, v
du = grad(u)
dv = grad(v)

#define jumps
jump_u = u-u.Other()
jump_v = v-v.Other()
jump_p = p-p.Other()
jump_q = q-q.Other()

#define average
average_dudn = 0.5*(grad(u)+grad(u.Other()))*n
average_dvdn = 0.5*(grad(v)+grad(v.Other()))*n
average_p = 0.5*(p+p.Other())
average_q = 0.5*(q+q.Other())


# Bilinear form
a = BilinearForm(X)
ah_dx = InnerProduct(du, dv)
ah_ds   = (eta/h)*jump_u*jump_v - (InnerProduct(jump_u, average_dvdn) + InnerProduct(jump_v, average_dudn))

bh_dx = - p*Trace(dv) + q*Trace(du)
bh_ds   = jump_v*n*average_p - jump_u*n*average_q

sh= h*InnerProduct(jump_p,jump_q)

a += (ah_dx + bh_dx)*dx
a += (ah_ds + bh_ds)*ds(skeleton=True)
a += sh*dx(skeleton=True)

# Linear form
f = LinearForm(X)

a.Assemble()
f.Assemble()

#boundary
g = CoefficientFunction((sin(np.pi*x), cos(np.pi*y)))
gfu.components[0].Set(g, BND, definedon=mesh.Boundaries("left|right|top|bottom"))

inv = a.mat.Inverse(freedofs=X.FreeDofs(), inverse="umfpack")
res = f.vec.CreateVector()
res.data = f.vec - a.mat*gfu.vec
gfu.vec.data += inv * res

Redraw()


NgException: VectorL2FESpace does not have an evaluator for BND!

In [19]:
help(FESpace)

Help on class FESpace in module ngsolve.comp:

class FESpace(NGS_Object)
 |  Finite Element Space
 |  
 |  Provides the functionality for finite element calculations.
 |  
 |  Some available FESpaces are:
 |  
 |  H1, HCurl, HDiv, L2, FacetFESpace, HDivDiv
 |  
 |  2 __init__ overloads:
 |    1) To create a registered FESpace
 |    2) To create a compound FESpace from multiple created FESpaces
 |  
 |  1)
 |  
 |  Parameters:
 |  
 |  type : string
 |    Type of the finite element space. This parameter is automatically
 |    set if the space is constructed with a generator function.
 |  
 |  mesh : ngsolve.Mesh
 |    Mesh on which the finite element space is defined on.
 |  
 |  kwargs : kwargs
 |    For a description of the possible kwargs have a look a bit further down.
 |  
 |  2)
 |  
 |  Parameters:
 |  
 |  spaces : list of ngsolve.FESpace
 |    List of the spaces for the compound finite element space
 |  
 |  kwargs : kwargs
 |    For a description of the possible kwargs have a 